## Importes 

In [1]:
# Utils
import pandas as pd
import numpy as np
from copy import deepcopy
from sklearn.preprocessing import Normalizer, StandardScaler
import warnings
from pathlib import Path

# Avaliação, Pontuação e Divisão
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error, mean_absolute_error

# Visualização de Dados
import matplotlib.pyplot as plt
import seaborn as sns

# Modelos
import keras
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Dense, Input
from sklearn.model_selection import train_test_split
from tensorflow.keras.optimizers import Adam

##
warnings.filterwarnings("ignore")

## Configurações

In [2]:
# configs
data_path =  Path('../data/02_outputs')
save_model_path = Path('../models/rnn_v1')

## Funções

In [3]:
def pre_model_data_prep(data):
    
    array = data.values
    
    y1 = array[:,0]
    y2 = array[:,1]
    features = array[:,2:]
    
    return y1, y2, features.astype('float32')

def build_model(neurons=128):
    
    # Define model layers.
    input_layer = Input(shape=(X_train.shape[1],))
    first_dense = Dense(units=neurons, activation='softmax')(input_layer)
    
    # Y1 output will be fed from the first dense
    y1_output = Dense(units='1', name='home_score_output')(first_dense)

    # Y2 output will be fed from the second dense
    second_dense = Dense(units=neurons, activation='softmax')(first_dense)
    y2_output = Dense(units='1', name='away_score_output')(second_dense)

    # Define the model with the input layer and a list of output layers
    model = Model(inputs=input_layer, outputs=[y1_output, y2_output])

    return model

def apply_scaler(features):
    
    scl = MinMaxScaler()
    scl.fit(features)
    scaled = scl.transform(features)
    
    return scaled

## Modelagem

Para segunda versão do moodelo, será utilizada uma abordagem diferente bem como um algoritmo diferente.

Será utilizada RN Redes Neurais.

In [4]:
# Carregando os dados e Preparando os dados
df = pd.read_csv(data_path / '01_matches_eco_score.csv')

#df['target'] = df.apply(create_target, axis=1)

df.drop(['match_date','home_team_name','away_team_name',
         'best_rank_winner', 'team_score_diff','draw',
         'home_winner','draw', 'away_winner'],
         axis=1, inplace=True)

df.dropna(inplace=True)

In [5]:
df.head()

home_team_score  away_team_score  year  home_rank  home_score  away_rank  \
0                4                1  1930       35.0      1566.0       41.0   
1                3                0  1930       14.0      1762.0       31.0   
2                2                1  1930       25.0      1658.0        9.0   
3                3                1  1930       37.0      1544.0       42.0   
4                1                0  1930        1.0      2062.0       35.0   

   away_score  home_n_participation  away_n_participation  rank_diff  \
0      1497.0                     0                     0       -6.0   
1      1593.0                     0                     0      -17.0   
2      1890.0                     0                     0       16.0   
3      1496.0                     0                     0       -5.0   
4      1566.0                     0                     0      -34.0   

   score_diff  
0        69.0  
1       169.0  
2      -232.0  
3        48.0  
4       496.0

In [6]:
# Utilizaremos as copas de 2012 e 2018 como teste e as outras como Treino
test = df[df['year'] > 2010]
val = df[df['year'] == 2010]
train = df[df['year'] < 2010]

test.drop('year', axis=1,inplace=True)
val.drop('year', axis=1,inplace=True)
train.drop('year', axis=1,inplace=True)

In [7]:
# Separando o output 1 (home team score), output 2 (away team score) e as variáveis
y1_train, y2_train, X_train = pre_model_data_prep(train)
y1_val, y2_val, X_val = pre_model_data_prep(val)
y1_test, y2_test, X_test = pre_model_data_prep(test)

In [8]:
# Normalizando os Dados
X_train, X_val, X_test = apply_scaler(X_train), apply_scaler(X_val), apply_scaler(X_test)

## Modelagem

In [9]:
for neurons in [32,64,128,256,512]:
        for batchs in [16,32,64]:
            for lr in [0.8,0.5,0.3,0.1]:
                try:
                    model = build_model(neurons)

                    optimizer = tf.keras.optimizers.Adam(learning_rate=lr)
                    model.compile(optimizer=optimizer,
                    loss={'home_score_output': 'mse', 'away_score_output': 'mse'},
                    metrics={'home_score_output': tf.keras.metrics.RootMeanSquaredError(),
                             'away_score_output': tf.keras.metrics.RootMeanSquaredError()})

                    # Treinando o modelo para 200 epochs
                    history = model.fit(X_train, (y1_train, y2_train),
                                    epochs=200, batch_size=batchs, validation_data=(X_val, (y1_val, y2_val)),
                    callbacks=[tf.keras.callbacks.ModelCheckpoint(save_model_path / f'model_{neurons}n_{batchs}b_{lr}lr.h5',
                                                            monitor='val_loss', mode='min',
                                                            save_best_only=True, verbose=1)])
                    
                except:
                    pass

Epoch 1/200
39/45 [=========================>....] - ETA: 0s - loss: 4.4713 - home_score_output_loss: 3.2432 - away_score_output_loss: 1.2282 - home_score_output_root_mean_squared_error: 1.8009 - away_score_output_root_mean_squared_error: 1.1082   
Epoch 1: val_loss improved from inf to 4.73455, saving model to ..\models\rnn_v1\model_32n_16b_0.8lr.h5
45/45 [==============================] - 2s 9ms/step - loss: 4.3776 - home_score_output_loss: 3.1665 - away_score_output_loss: 1.2111 - home_score_output_root_mean_squared_error: 1.7795 - away_score_output_root_mean_squared_error: 1.1005 - val_loss: 4.7345 - val_home_score_output_loss: 3.7899 - val_away_score_output_loss: 0.9446 - val_home_score_output_root_mean_squared_error: 1.9468 - val_away_score_output_root_mean_squared_error: 0.9719
Epoch 2/200
39/45 [=========================>....] - ETA: 0s - loss: 4.3787 - home_score_output_loss: 3.0655 - away_score_output_loss: 1.3133 - home_score_output_root_mean_squared_error: 1.7508 - away_sco

Epoch 12/200
37/45 [=======================>......] - ETA: 0s - loss: 4.5235 - home_score_output_loss: 3.3328 - away_score_output_loss: 1.1907 - home_score_output_root_mean_squared_error: 1.8256 - away_score_output_root_mean_squared_error: 1.0912
Epoch 12: val_loss did not improve from 2.88607
45/45 [==============================] - 0s 2ms/step - loss: 4.2466 - home_score_output_loss: 3.1236 - away_score_output_loss: 1.1229 - home_score_output_root_mean_squared_error: 1.7674 - away_score_output_root_mean_squared_error: 1.0597 - val_loss: 3.0467 - val_home_score_output_loss: 1.7943 - val_away_score_output_loss: 1.2524 - val_home_score_output_root_mean_squared_error: 1.3395 - val_away_score_output_root_mean_squared_error: 1.1191
Epoch 13/200
37/45 [=======================>......] - ETA: 0s - loss: 4.3385 - home_score_output_loss: 3.1689 - away_score_output_loss: 1.1696 - home_score_output_root_mean_squared_error: 1.7801 - away_score_output_root_mean_squared_error: 1.0815
Epoch 13: val_l

42/45 [===========================>..] - ETA: 0s - loss: 4.0319 - home_score_output_loss: 2.9127 - away_score_output_loss: 1.1192 - home_score_output_root_mean_squared_error: 1.7067 - away_score_output_root_mean_squared_error: 1.0579
Epoch 34: val_loss did not improve from 2.71315
45/45 [==============================] - 0s 2ms/step - loss: 4.1128 - home_score_output_loss: 2.9545 - away_score_output_loss: 1.1583 - home_score_output_root_mean_squared_error: 1.7189 - away_score_output_root_mean_squared_error: 1.0762 - val_loss: 3.9933 - val_home_score_output_loss: 2.3511 - val_away_score_output_loss: 1.6423 - val_home_score_output_root_mean_squared_error: 1.5333 - val_away_score_output_root_mean_squared_error: 1.2815
Epoch 35/200
42/45 [===========================>..] - ETA: 0s - loss: 4.0937 - home_score_output_loss: 2.9161 - away_score_output_loss: 1.1776 - home_score_output_root_mean_squared_error: 1.7077 - away_score_output_root_mean_squared_error: 1.0852
Epoch 35: val_loss did not i

43/45 [===========================>..] - ETA: 0s - loss: 4.3387 - home_score_output_loss: 2.8812 - away_score_output_loss: 1.4575 - home_score_output_root_mean_squared_error: 1.6974 - away_score_output_root_mean_squared_error: 1.2073
Epoch 56: val_loss did not improve from 2.71122
45/45 [==============================] - 0s 2ms/step - loss: 4.3686 - home_score_output_loss: 2.8957 - away_score_output_loss: 1.4729 - home_score_output_root_mean_squared_error: 1.7017 - away_score_output_root_mean_squared_error: 1.2136 - val_loss: 3.4999 - val_home_score_output_loss: 2.4718 - val_away_score_output_loss: 1.0281 - val_home_score_output_root_mean_squared_error: 1.5722 - val_away_score_output_root_mean_squared_error: 1.0140
Epoch 57/200
41/45 [==========================>...] - ETA: 0s - loss: 4.3022 - home_score_output_loss: 3.1165 - away_score_output_loss: 1.1857 - home_score_output_root_mean_squared_error: 1.7654 - away_score_output_root_mean_squared_error: 1.0889
Epoch 57: val_loss did not i

42/45 [===========================>..] - ETA: 0s - loss: 4.4663 - home_score_output_loss: 3.0630 - away_score_output_loss: 1.4033 - home_score_output_root_mean_squared_error: 1.7501 - away_score_output_root_mean_squared_error: 1.1846
Epoch 78: val_loss did not improve from 2.71122
45/45 [==============================] - 0s 2ms/step - loss: 4.5074 - home_score_output_loss: 3.1305 - away_score_output_loss: 1.3769 - home_score_output_root_mean_squared_error: 1.7693 - away_score_output_root_mean_squared_error: 1.1734 - val_loss: 3.2926 - val_home_score_output_loss: 2.3453 - val_away_score_output_loss: 0.9473 - val_home_score_output_root_mean_squared_error: 1.5314 - val_away_score_output_root_mean_squared_error: 0.9733
Epoch 79/200
40/45 [=========================>....] - ETA: 0s - loss: 3.9133 - home_score_output_loss: 2.7754 - away_score_output_loss: 1.1379 - home_score_output_root_mean_squared_error: 1.6660 - away_score_output_root_mean_squared_error: 1.0667
Epoch 79: val_loss did not i

...

10/12 [========================>.....] - ETA: 0s - loss: 3.1517 - home_score_output_loss: 2.2186 - away_score_output_loss: 0.9331 - home_score_output_root_mean_squared_error: 1.4895 - away_score_output_root_mean_squared_error: 0.9660
Epoch 92: val_loss did not improve from 2.26135
12/12 [==============================] - 0s 8ms/step - loss: 3.1216 - home_score_output_loss: 2.1893 - away_score_output_loss: 0.9323 - home_score_output_root_mean_squared_error: 1.4796 - away_score_output_root_mean_squared_error: 0.9656 - val_loss: 2.8012 - val_home_score_output_loss: 1.8689 - val_away_score_output_loss: 0.9323 - val_home_score_output_root_mean_squared_error: 1.3671 - val_away_score_output_root_mean_squared_error: 0.9656
Epoch 93/200
10/12 [========================>.....] - ETA: 0s - loss: 3.1164 - home_score_output_loss: 2.1700 - away_score_output_loss: 0.9464 - home_score_output_root_mean_squared_error: 1.4731 - away_score_output_root_mean_squared_error: 0.9728
Epoch 93: val_loss did not i

10/12 [========================>.....] - ETA: 0s - loss: 3.0084 - home_score_output_loss: 2.1148 - away_score_output_loss: 0.8936 - home_score_output_root_mean_squared_error: 1.4542 - away_score_output_root_mean_squared_error: 0.9453
Epoch 114: val_loss did not improve from 2.26135
12/12 [==============================] - 0s 8ms/step - loss: 3.0084 - home_score_output_loss: 2.1221 - away_score_output_loss: 0.8863 - home_score_output_root_mean_squared_error: 1.4567 - away_score_output_root_mean_squared_error: 0.9414 - val_loss: 2.5714 - val_home_score_output_loss: 1.7689 - val_away_score_output_loss: 0.8025 - val_home_score_output_root_mean_squared_error: 1.3300 - val_away_score_output_root_mean_squared_error: 0.8958
Epoch 115/200
10/12 [========================>.....] - ETA: 0s - loss: 3.0950 - home_score_output_loss: 2.1831 - away_score_output_loss: 0.9119 - home_score_output_root_mean_squared_error: 1.4775 - away_score_output_root_mean_squared_error: 0.9549
Epoch 115: val_loss did no

10/12 [========================>.....] - ETA: 0s - loss: 2.8723 - home_score_output_loss: 1.9520 - away_score_output_loss: 0.9203 - home_score_output_root_mean_squared_error: 1.3971 - away_score_output_root_mean_squared_error: 0.9593
Epoch 136: val_loss did not improve from 2.26135
12/12 [==============================] - 0s 8ms/step - loss: 2.9984 - home_score_output_loss: 2.0788 - away_score_output_loss: 0.9196 - home_score_output_root_mean_squared_error: 1.4418 - away_score_output_root_mean_squared_error: 0.9590 - val_loss: 2.7946 - val_home_score_output_loss: 2.0489 - val_away_score_output_loss: 0.7457 - val_home_score_output_root_mean_squared_error: 1.4314 - val_away_score_output_root_mean_squared_error: 0.8635
Epoch 137/200
10/12 [========================>.....] - ETA: 0s - loss: 3.0295 - home_score_output_loss: 2.1337 - away_score_output_loss: 0.8958 - home_score_output_root_mean_squared_error: 1.4607 - away_score_output_root_mean_squared_error: 0.9465
Epoch 137: val_loss did no

10/12 [========================>.....] - ETA: 0s - loss: 3.0093 - home_score_output_loss: 2.1109 - away_score_output_loss: 0.8984 - home_score_output_root_mean_squared_error: 1.4529 - away_score_output_root_mean_squared_error: 0.9478
Epoch 158: val_loss did not improve from 2.26135
12/12 [==============================] - 0s 8ms/step - loss: 2.9718 - home_score_output_loss: 2.0656 - away_score_output_loss: 0.9063 - home_score_output_root_mean_squared_error: 1.4372 - away_score_output_root_mean_squared_error: 0.9520 - val_loss: 2.6307 - val_home_score_output_loss: 1.8806 - val_away_score_output_loss: 0.7501 - val_home_score_output_root_mean_squared_error: 1.3714 - val_away_score_output_root_mean_squared_error: 0.8661
Epoch 159/200
10/12 [========================>.....] - ETA: 0s - loss: 2.9491 - home_score_output_loss: 2.0636 - away_score_output_loss: 0.8855 - home_score_output_root_mean_squared_error: 1.4365 - away_score_output_root_mean_squared_error: 0.9410
Epoch 159: val_loss did no

10/12 [========================>.....] - ETA: 0s - loss: 2.9222 - home_score_output_loss: 2.0490 - away_score_output_loss: 0.8731 - home_score_output_root_mean_squared_error: 1.4314 - away_score_output_root_mean_squared_error: 0.9344
Epoch 180: val_loss did not improve from 2.26135
12/12 [==============================] - 0s 8ms/step - loss: 2.9013 - home_score_output_loss: 2.0284 - away_score_output_loss: 0.8729 - home_score_output_root_mean_squared_error: 1.4242 - away_score_output_root_mean_squared_error: 0.9343 - val_loss: 3.2853 - val_home_score_output_loss: 2.1299 - val_away_score_output_loss: 1.1553 - val_home_score_output_root_mean_squared_error: 1.4594 - val_away_score_output_root_mean_squared_error: 1.0749
Epoch 181/200
10/12 [========================>.....] - ETA: 0s - loss: 2.9477 - home_score_output_loss: 2.0307 - away_score_output_loss: 0.9170 - home_score_output_root_mean_squared_error: 1.4250 - away_score_output_root_mean_squared_error: 0.9576
Epoch 181: val_loss did no

## Teste

In [10]:
test_model = tf.keras.models.load_model(save_model_path / 'model_256n_32b_0.5lr.h5')
predictions = test_model.predict(X_test)

4/4 [==============================] - 0s 3ms/step


In [11]:
y1_preds = predictions[0]
y2_preds = predictions[1]

In [12]:
r_y1_preds = [np.round(x) for x in y1_preds]
r_y2_preds = [np.round(x) for x in y2_preds]

In [13]:
acc = 1 - np.sqrt(mean_squared_error(y2_test, r_y2_preds))
acc

-0.18255549552653139

In [14]:
r_y2_preds

[array([1.], dtype=float32),
 array([1.], dtype=float32),
 array([2.], dtype=float32),
 array([1.], dtype=float32),
 array([1.], dtype=float32),
 array([1.], dtype=float32),
 array([2.], dtype=float32),
 array([2.], dtype=float32),
 array([2.], dtype=float32),
 array([1.], dtype=float32),
 array([1.], dtype=float32),
 array([1.], dtype=float32),
 array([2.], dtype=float32),
 array([2.], dtype=float32),
 array([1.], dtype=float32),
 array([1.], dtype=float32),
 array([1.], dtype=float32),
 array([2.], dtype=float32),
 array([1.], dtype=float32),
 array([2.], dtype=float32),
 array([1.], dtype=float32),
 array([2.], dtype=float32),
 array([1.], dtype=float32),
 array([1.], dtype=float32),
 array([2.], dtype=float32),
 array([2.], dtype=float32),
 array([1.], dtype=float32),
 array([1.], dtype=float32),
 array([2.], dtype=float32),
 array([1.], dtype=float32),
 array([2.], dtype=float32),
 array([2.], dtype=float32),
 array([2.], dtype=float32),
 array([1.], dtype=float32),
 array([2.], d